In [2]:
!pip3 install pandas

!pip3 install numpy

!pip3 install beautifulsoup4


!pip3 install --upgrade pip


In [3]:
import pandas as pd
import requests
import numpy as np 
import time
from bs4 import BeautifulSoup
import string



/Users/arhan/Desktop/ML_ufc/myenv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [4]:

base_url = 'http://ufcstats.com/statistics/fighters' 
characters = string.ascii_lowercase 
all_fighters = []
fighters = []
for char in characters:
    url = f"{base_url}?char={char}&page=all"
    try:
        response = requests.get(url)
        response.raise_for_status()  

        html_content = response.text
        soup = BeautifulSoup(html_content, 'html.parser')

        table_rows = soup.select('.b-statistics__table-row')

        if not table_rows:
            print("No table rows found. Check the HTML structure or the selector.")
        else:
            for row in table_rows[1:]:  # Skip the header row
                cells = row.find_all('td')
                if len(cells) >= 9:  # Check if there are at least 9 cells
                    name = f"{cells[0].get_text(strip=True)} {cells[1].get_text(strip=True)}"  # First and Last Name
                    wins = cells[7].get_text(strip=True)  # Wins
                    losses = cells[8].get_text(strip=True)  # Losses
                    weight = cells[4].get_text(strip=True)  # Weight
                    fighters.append({'name': name, 'wins': wins, 'losses': losses, 'weight': weight})


        print(fighters)

    except requests.exceptions.RequestException as e:
        print(f"An error occurred: {e}")


[{'name': 'Tom Aaron', 'wins': '5', 'losses': '3', 'weight': '155 lbs.'}, {'name': 'Danny Abbadi', 'wins': '4', 'losses': '6', 'weight': '155 lbs.'}, {'name': 'Nariman Abbasov', 'wins': '28', 'losses': '4', 'weight': '155 lbs.'}, {'name': 'David Abbott', 'wins': '10', 'losses': '15', 'weight': '265 lbs.'}, {'name': 'Hamdy Abdelwahab', 'wins': '5', 'losses': '0', 'weight': '264 lbs.'}, {'name': 'Mansur Abdul-Malik', 'wins': '7', 'losses': '0', 'weight': '185 lbs.'}, {'name': 'Shamil Abdurakhimov', 'wins': '20', 'losses': '8', 'weight': '235 lbs.'}, {'name': 'Hiroyuki Abe', 'wins': '8', 'losses': '15', 'weight': '145 lbs.'}, {'name': 'Daichi Abe', 'wins': '6', 'losses': '2', 'weight': '170 lbs.'}, {'name': 'Papy Abedi', 'wins': '10', 'losses': '4', 'weight': '185 lbs.'}, {'name': 'Ricardo Abreu', 'wins': '5', 'losses': '1', 'weight': '185 lbs.'}, {'name': 'Klidson Abreu', 'wins': '15', 'losses': '4', 'weight': '205 lbs.'}, {'name': 'Cyborg Abreu', 'wins': '0', 'losses': '0', 'weight': '-

In [5]:
fighters_df = pd.DataFrame(fighters)

In [6]:
fighters_df = fighters_df[~((pd.to_numeric(fighters_df['wins']) == 0) & (pd.to_numeric(fighters_df['losses']) == 0))]

In [10]:
def calc_rating( wins , losses):
    result = (20/(1.1 + np.exp(-.12*(wins-1)))+3)/(np.exp(0.022*(losses+1))/4)
    return result

def calc_Gfactor( x):
    result = 30+(300/(1 + np.exp(-.25*(x-70))))
    return result

fighters_df['wins'] = pd.to_numeric(fighters_df['wins'], errors='coerce')
fighters_df['losses'] = pd.to_numeric(fighters_df['losses'], errors='coerce')

fighters_df['rating'] = fighters_df.apply(lambda row: calc_rating(row['wins'], row['losses']), axis=1)
fighters_df['Gfactor'] = fighters_df['rating'].apply(calc_Gfactor)

display(fighters_df)

fighters_df.to_csv("static_data.csv", index=False)

name  wins  losses    weight     rating     Gfactor
0            Tom Aaron     5       3  155 lbs.  53.612809   34.906179
1         Danny Abbadi     4       6  155 lbs.  48.437492   31.361527
2      Nariman Abbasov    28       4  155 lbs.  73.661704  244.232762
3         David Abbott    10      15  265 lbs.  47.521457   31.083858
4     Hamdy Abdelwahab     5       0  264 lbs.  57.270635   41.950705
...                ...   ...     ...       ...        ...         ...
4256     Dave Zitanick     5       7  170 lbs.  49.096513   31.604078
4257       Alex Zuniga     6       3  145 lbs.  55.421659   37.640023
4258     George Zuniga     3       1  185 lbs.  52.061835   33.346859
4259      Allan Zuniga    13       1  155 lbs.  68.746315  156.683954
4260    Virgil Zwicker    15       6  205 lbs.  63.601279   80.407897

[4242 rows x 6 columns]

In [11]:
display(fighters_df.nlargest(100, 'Gfactor'))


name  wins  losses    weight     rating     Gfactor
2764    Khabib Nurmagomedov    29       0  155 lbs.  80.705823  310.686892
2708  Julio Cesar Neves Jr.    33       1  145 lbs.  79.746268  305.872068
1816              Jon Jones    27       1  248 lbs.  78.394112  297.228009
2288        Islam Makhachev    26       1  155 lbs.  78.066486  294.759363
194        Khusein Askhabov    23       1  145 lbs.  76.840156  284.052399
...                     ...   ...     ...       ...        ...         ...
1929     Aliaskhab Khizriev    14       0  185 lbs.  71.472540  207.302474
2647      Azamat Murzakanov    14       0  205 lbs.  71.472540  207.302474
1028           Leon Edwards    22       4  170 lbs.  71.460881  207.091048
1936          Dong Hyun Kim    22       4  170 lbs.  71.460881  207.091048
45              Amir Albazi    17       2  125 lbs.  71.309016  204.327330

[100 rows x 6 columns]